In [1]:
import nltk
import spacy
import re
import unidecode
from nltk.corpus import stopwords
from numpy import *
import pandas as pd 
import requests 
import re
import pdfplumber
from gensim.models import Word2Vec
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np


In [2]:
# Download Greek stopwords
nltk.download('stopwords')
greek_stopwords = set(stopwords.words('greek'))

# Load Greek NLP model
#!python -m spacy download el_core_news_sm
nlp = spacy.load('el_core_news_sm')  # Greek NLP model


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\steve\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
def preprocess_text(text):
    #process our text and return it as embeddings
    # Remove punctuation and numbers (keeping Greek characters)
    text = re.sub(r"[^a-zA-ZάέήίόύώΆΈΉΊΌΎΏα-ωΑ-Ω\s]", "", text)

    # Convert to lowercase
    text = text.lower()

    # Split text into sentences
    sentences = text.split('\n')  # You can also use sentence segmentation via spaCy if needed
    
    # Initialize an empty list to hold the tokenized sentences
    tokenized_sentences = []

    # Tokenize each sentence
    for sentence in sentences:
        # Tokenize using spaCy
        doc = nlp(sentence)
        
        # Extract tokens (words) and filter out stopwords and punctuation
        tokens = [token.lemma_ for token in doc if token.text not in greek_stopwords and not token.is_punct]
        
        # Filter out short tokens (length > 2)
        tokens = [token for token in tokens if len(token) > 2]

        # Add the tokens of the sentence to the list of sentences
        if tokens:
            tokenized_sentences.append(tokens)

    return tokenized_sentences


Let us create a list of books , upon which we will train our model.

In [4]:
books = ['https://1oholargou.wordpress.com/wp-content/uploads/2012/08/13078091-31328.pdf',
         #'https://derkamerad.com/wp-content/uploads/2016/09/cebcceb1cf84cf89cebcceb5cebdceb1-cf87cf89cebcceb1cf84ceb1-ceb4ceb9ceb4cf89-cf83cf89cf84ceb7cf81ceb9cebfcf85.pdff'
        'https://schoolpress.sch.gr/periodista/files/2022/02/%CE%A4%CE%BF-%CE%9C%CE%BF%CE%BD%CF%8C%CE%B3%CF%81%CE%B1%CE%BC%CE%BC%CE%B11.pdf',
        'http://7gym-athin.att.sch.gr/wordpress/wp-content/uploads/2020/03/Aiolike-Ge-Elias-Benezes.pdf',
        'https://books.shopflix.gr/9786180103106.pdf',
         'https://www.patakis.gr/files/1187291.pdf'#,
         #'https://manifestolibrary.noblogs.org/files/2020/10/441339144-%CE%86%CF%81%CE%B7%CF%82-%CE%91%CE%BB%CE%B5%CE%BE%CE%AC%CE%BD%CE%B4%CF%81%CE%BF%CF%85-%CF%84%CE%BF-%CE%BA%CE%B9%CE%B2%CF%8E%CF%84%CE%B9%CE%BF-pdf.pdf',
         #'https://blogs.sch.gr/idaragiannis/files/2017/02/ena-paidi-metraei-t-astra.pdf'
 ]

In [5]:
def download_book(book, i):
    
    #download the book and save it as a pdf file
    response = requests.get(book)
    pdf_path = f"{i}.pdf"
    with open(pdf_path, "wb") as f:
        f.write(response.content)
        
    #save the pdf as a string
    with pdfplumber.open(pdf_path) as pdf:
        text = ""
        for page in pdf.pages:
            text += page.extract_text() + "\n"  
    return text

Download our books, save them as pdfs, convert them to strings, tokenize them, and add them to our corpus.

In [6]:
all_tokens = []
corpus = []
for i,book in enumerate(books):
    book_text = download_book(book, i)
    tokens = preprocess_text(book_text)
    book_text_processed = " ".join(word for sentence in tokens for word in sentence)
    corpus.append(book_text_processed)
    all_tokens.extend(tokens)

In [7]:
print(all_tokens)

[['ηλιο', 'βενεζη'], ['ακαδημία', 'αθηνών'], ['νούμερο'], ['βιβλιο', 'σκλαβια'], ['εισαγωγή', 'δημήτρης', 'δασκαλόπουλος'], ['τεσσαρακοστος', 'εβδομος', 'εκδοση'], ['βιβλιοπωλειον', 'εστια'], ['κολλαρο', 'σιος'], ['αθηνα'], ['νούμερο', 'είμαι', 'ίδιος', 'ταυτότητα', 'συγγραφέα', 'παιδί'], ['δεκαοκτώς', 'χρόνος', 'οδηγώ', 'από', 'τούρκους', 'σε ο', 'κάτεργα', 'ανατολή'], ['βιβλίο', 'είμαι', 'ένας', 'συγκλονιστικός', 'χρονικός', 'γραμμένος', 'αίμα', 'όπως', 'επισημαίνω'], ['βενέζης', 'προσθέτοντα', 'λέω', 'καυτής', 'ύλη', 'σάρκα', 'στάζω'], ['αίμα', 'μου', 'πλημμυρίζω', 'σελίδα', 'αρχικός', 'μορφή', 'γράφτηκε'], ['ξαναδουλεύτηκε', 'οπότε', 'εκδόθηκε', 'πρώτος', 'φορά', 'επιτυχία'], ['σημείωσε', 'είμαι', 'τεράστιος', 'ακόμα', 'έξω', 'από', 'ελληνικός', 'χώρος'], ['ηλία', 'βενέζης', 'βιβλίομαρτυρία', 'είμαι', 'γραώνμ', 'πρώτος', 'πρόσωπος'], ['πραγματικός', 'όνομα', 'αφηγητήσυγγραφέα', 'γεννήθηκε', 'αβαλίς', 'ήρθε'], ['Ελλάδα', 'μικρασιατικός', 'καταστροφή', 'θεωρώ', 'ένας', 'από'], ['κυρι

In [8]:
print(corpus)

['ηλιο βενεζη ακαδημία αθηνών νούμερο βιβλιο σκλαβια εισαγωγή δημήτρης δασκαλόπουλος τεσσαρακοστος εβδομος εκδοση βιβλιοπωλειον εστια κολλαρο σιος αθηνα νούμερο είμαι ίδιος ταυτότητα συγγραφέα παιδί δεκαοκτώς χρόνος οδηγώ από τούρκους σε ο κάτεργα ανατολή βιβλίο είμαι ένας συγκλονιστικός χρονικός γραμμένος αίμα όπως επισημαίνω βενέζης προσθέτοντα λέω καυτής ύλη σάρκα στάζω αίμα μου πλημμυρίζω σελίδα αρχικός μορφή γράφτηκε ξαναδουλεύτηκε οπότε εκδόθηκε πρώτος φορά επιτυχία σημείωσε είμαι τεράστιος ακόμα έξω από ελληνικός χώρος ηλία βενέζης βιβλίομαρτυρία είμαι γραώνμ πρώτος πρόσωπος πραγματικός όνομα αφηγητήσυγγραφέα γεννήθηκε αβαλίς ήρθε Ελλάδα μικρασιατικός καταστροφή θεωρώ ένας από κυριότερους εκπροσώπους γενιά νεοελληνικός πεζογραφία τεσσαρακοστή τρίτος έκδοση βιβλίου ηλία βενέζη νούμερο αναστοιχειοθετήθηκε προτάχθηκε αυτός εισαγωγικός κείμενο δημήτρη δασκαλόπουλου νέος έκδοση κυκλοφόρησε φεβρουάριο σειρά νεοελληνικός λογοτεχνία      τεσσαρακοστός έβδομος έκδοση σεπτέμβριος βιβλιοπω

In [9]:
# response = requests.get('https://1oholargou.wordpress.com/wp-content/uploads/2012/08/13078091-31328.pdf')
# pdf_path = "downloaded.pdf"
# with open(pdf_path, "wb") as f:
#     f.write(response.content)

In [10]:

# pdf_path = "downloaded.pdf"  

# with pdfplumber.open(pdf_path) as pdf:
#     text = ""
#     for page in pdf.pages:
#         text += page.extract_text() + "\n"  

# print(text) 


In [11]:
# tokens = preprocess_text(text)
# print(tokens)


Let us train a tf idf vectorizer on these sentences!

In [12]:
vectorizer = TfidfVectorizer()
tfidf_matrix = vectorizer.fit_transform(corpus)

# Get feature names (words) and their scores
feature_names = vectorizer.get_feature_names_out()
tfidf_scores = np.array(tfidf_matrix.mean(axis=0)).flatten()

# Create a dictionary mapping words to their TF-IDF scores
word_tfidf = dict(zip(feature_names, tfidf_scores))

Check the words with the highest tf idf score, aka common words that are non distinctive!

In [13]:
# Inspect top TF-IDF scores
print("Top 10 words by TF-IDF score:")
sorted_tfidf = sorted(word_tfidf.items(), key=lambda x: x[1], reverse=True)
for word, score in sorted_tfidf[:100]:
    print(word, score)

Top 10 words by TF-IDF score:
μου 0.32397960401356374
ένας 0.3196618907628709
είμαι 0.2606016778656109
από 0.18407134103533004
εγώ 0.18269673034417022
έχω 0.17552937475134947
αυτός 0.13267072479881323
σε 0.1325435589163687
στός 0.09583869406355493
άλλος 0.08790474805217614
πού 0.0807326572499569
όλος 0.07814350252280938
λέγω 0.06182009025498199
γιά 0.06133676420067516
ακός 0.06064018807561348
σου 0.05584860394194914
σαν 0.0530854825125571
πολύ 0.051678471214852334
μές 0.049836120913048565
λέει 0.04953154385429081
σαμαράκη 0.04821959195320811
μεγάλος 0.046837661248107634
εκδοσεις 0.04616769442328436
ψυχογιος 0.04616769442328436
ώρα 0.04541119495591843
δυο 0.044699030378636234
κάνω 0.04427656348276209
μάτι 0.042938298092923564
τώρα 0.04272942416500965
χέρι 0.04180425236928413
κάτι 0.04105714804964472
όχι 0.04100502076159058
γιατί 0.040130148135638186
πιο 0.03980416668640212
μάνατζερ 0.03898605306855124
έτσι 0.038562002415842754
εκεί 0.03855288555108635
όταν 0.038457420711380995
δέν 0.038

Define a function that filters words, based on their tf idf score, since we do not care about words that are all over our documents, because they are not distinctive in terms of our target word!

In [14]:
tfidf_threshold = np.percentile(list(word_tfidf.values()), 75)  # Top 25% most common words

# Function to filter words based on TF-IDF scores
def filter_words_by_tfidf(similar_words, word_tfidf, threshold):
    return [(word, score) for word, score in similar_words if word_tfidf.get(word, 0) > threshold]

In [15]:
print(tokens)

[['αηδονοπιτα'], ['τoy', 'ιδιoy'], ['φραουστ', 'νέος', 'σύνορο', 'λιβάνη', 'νέος', 'έκδοση'], ['αναθεωρημένη', 'εκδόσεις', 'πατάκη'], ['αποσπασμα', 'βιβλιο', 'ωκεανου', 'εκδόσεις', 'πατάκη'], ['νέος', 'έκδοση', 'εκδόσεις', 'πατάκη'], ['ψιχος', 'εκεινου', 'καλοκαιριος', 'εκδόσεις', 'πατάκη'], ['σκι', 'πεταλουδα', 'εκδόσεις', 'πατάκη'], ['αηδονοπιτα', 'εκδόσεις', 'πατάκη'], ['ανεμωλιο', 'εκδόσεις', 'πατάκη'], ['σκηνος', 'βιο', 'ματιας', 'αλμοσινο', 'εκδόσεις', 'πατάκη'], ['λιγες', 'ένας', 'νυχτος', 'εκδόσεις', 'πατάκη'], ['ισιδωρος', 'ζουργος'], ['αηδονοπιτα'], ['μυθιστόρημα'], ['θέση', 'υπογραφή', 'δικαιούχου', 'δικαίωμα', 'πνευματικός', 'ιδιοκτησία'], ['εφόσον', 'αυτός', 'προβλέπω', 'από', 'σύμβαση'], ['παρόν', 'έργο', 'πνευματικός', 'ιδιοκτησία', 'προστατεύω', 'διάταξη', 'ελληνικός'], ['μοθεσία', 'όπως', 'έχω', 'τροποποιώ', 'ισχύω', 'σήμερα', 'διεθνής', 'σύμβαση'], ['πνευματικός', 'ιδιοκτησία', 'απαγορεύω', 'απόλυτα', 'άνευ', 'γραπτός', 'αδεία', 'εκδότη'], ['οποιονδήποτε', 'τρόπος', '

In [16]:
for sentence in tokens:
    for word in sentence:
        if word == 'γυναίκα':
            print('True')
            

True
True
True


In [17]:

# Train Word2Vec Model
model = Word2Vec(all_tokens, vector_size=100, window=5, min_count=3, workers=4)

# Save model for future use
model.save("greek_word2vec.model")


In [18]:
word_index = model.wv.key_to_index.get('μαύρος', 'Word not found in vocabulary')

print(f"Index of '': {word_index}")

Index of '': 1104


In [19]:
vocab = model.wv.index_to_key  # List of words in the model's vocabulary
print(vocab[146]) 

επειδή


In [20]:

similar_words_woman = model.wv.most_similar('γυναίκα', topn=5000)
similar_words_man = model.wv.most_similar('άντρας', topn=5000)

Similar words to man, without tf idf

In [21]:
print("\nSimilar words to 'γυναίκα':")
for word in similar_words_woman:
    print(word)


Similar words to 'γυναίκα':
('μονάχα', 0.9997975826263428)
('τότης', 0.9997918605804443)
('κάτι', 0.999791145324707)
('κάνω', 0.9997882843017578)
('νέος', 0.9997853636741638)
('πάει', 0.9997848868370056)
('εδώ', 0.999784529209137)
('στρατιώτης', 0.9997822046279907)
('όλος', 0.9997767210006714)
('πώς', 0.9997692704200745)
('δίνω', 0.9997648000717163)
('κυνηγός', 0.9997633099555969)
('όταν', 0.9997618198394775)
('πρόσωπό', 0.9997600317001343)
('απάνω', 0.9997587203979492)
('φωνάζω', 0.9997552633285522)
('όσο', 0.9997519850730896)
('ίσαμε', 0.9997506737709045)
('παππός', 0.9997462630271912)
('πρέπει', 0.9997459650039673)
('άνθρωπος', 0.9997458457946777)
('εκεί', 0.9997448921203613)
('όλο', 0.9997444748878479)
('φωνή', 0.9997417330741882)
('τόπος', 0.9997417330741882)
('τούτος', 0.9997406005859375)
('αυτός', 0.9997401237487793)
('σαν', 0.999739944934845)
('μικρός', 0.9997394680976868)
('έχω', 0.999739408493042)
('πλάι', 0.9997388124465942)
('καμιά', 0.9997369050979614)
('πάντα', 0.9997365

Similar words to woman, without tf idf

In [22]:
print("\nSimilar words to 'άνδρας':")
for word in similar_words_man:
    print(word)


Similar words to 'άνδρας':
('πώς', 0.9997640252113342)
('νέος', 0.9997550249099731)
('πάντα', 0.9997438192367554)
('όταν', 0.9997391104698181)
('χωρίς', 0.9997380971908569)
('πλάι', 0.99973464012146)
('κάνω', 0.999732494354248)
('στρατιώτης', 0.9997281432151794)
('εδώ', 0.9997279047966003)
('ίδιος', 0.9997266530990601)
('όπου', 0.9997217059135437)
('μονάχα', 0.9997165203094482)
('φωνή', 0.9997162222862244)
('ντόρις', 0.9997158646583557)
('δίνω', 0.9997156262397766)
('όλος', 0.9997139573097229)
('κοντά', 0.9997132420539856)
('φωνάζω', 0.9997124075889587)
('γυναίκα', 0.9997096657752991)
('τέλος', 0.9997091293334961)
('βλέπω', 0.9997085332870483)
('τούτος', 0.9997062683105469)
('θάλασσα', 0.9997047781944275)
('όπως', 0.9997042417526245)
('ίσαμε', 0.9997039437294006)
('άνθρωπος', 0.9997020363807678)
('τώρα', 0.999701976776123)
('όμως', 0.9996985197067261)
('μικρός', 0.9996974468231201)
('σαν', 0.9996969103813171)
('ανατολή', 0.9996965527534485)
('κυνηγός', 0.9996938705444336)
('μένω', 0.9

In [23]:
word_at_index_656 = model.wv.index_to_key[656]
print(word_at_index_656)

ψαλμός


Use tf idf for both groups, in order to filter non distinctive words (aka words that appear all over the book, and not just our target tokens)

In [24]:

similar_words_man_filtered = filter_words_by_tfidf(similar_words_man, word_tfidf, tfidf_threshold)
similar_words_woman_filtered = filter_words_by_tfidf(similar_words_woman, word_tfidf, tfidf_threshold)


In [35]:
print("\nFiltered similar words to 'γυναίκα':")
for word, score in similar_words_woman_filtered:
    print(word, score)


Filtered similar words to 'γυναίκα':
μονάχα 0.9997975826263428
τότης 0.9997918605804443
κάτι 0.999791145324707
κάνω 0.9997882843017578
νέος 0.9997853636741638
πάει 0.9997848868370056
εδώ 0.999784529209137
στρατιώτης 0.9997822046279907
όλος 0.9997767210006714
πώς 0.9997692704200745
δίνω 0.9997648000717163
κυνηγός 0.9997633099555969
όταν 0.9997618198394775
πρόσωπό 0.9997600317001343
απάνω 0.9997587203979492
φωνάζω 0.9997552633285522
όσο 0.9997519850730896
ίσαμε 0.9997506737709045
παππός 0.9997462630271912
πρέπει 0.9997459650039673
άνθρωπος 0.9997458457946777
εκεί 0.9997448921203613
όλο 0.9997444748878479
φωνή 0.9997417330741882
τόπος 0.9997417330741882
τούτος 0.9997406005859375
αυτός 0.9997401237487793
σαν 0.999739944934845
μικρός 0.9997394680976868
έχω 0.999739408493042
πλάι 0.9997388124465942
καμιά 0.9997369050979614
πάντα 0.9997365474700928
καρδιά 0.9997363090515137
ίδιος 0.9997360110282898
αίμα 0.9997354745864868
ύστερα 0.9997349977493286
αργά 0.9997349381446838
μέσα 0.9997332096099

In [34]:
print("\nFiltered similar words to 'άνδρας':")
for word, score in similar_words_man:
    print(word, score)


Filtered similar words to 'άνδρας':
πώς 0.9997640252113342
νέος 0.9997550249099731
πάντα 0.9997438192367554
όταν 0.9997391104698181
χωρίς 0.9997380971908569
πλάι 0.99973464012146
κάνω 0.999732494354248
στρατιώτης 0.9997281432151794
εδώ 0.9997279047966003
ίδιος 0.9997266530990601
όπου 0.9997217059135437
μονάχα 0.9997165203094482
φωνή 0.9997162222862244
ντόρις 0.9997158646583557
δίνω 0.9997156262397766
όλος 0.9997139573097229
κοντά 0.9997132420539856
φωνάζω 0.9997124075889587
γυναίκα 0.9997096657752991
τέλος 0.9997091293334961
βλέπω 0.9997085332870483
τούτος 0.9997062683105469
θάλασσα 0.9997047781944275
όπως 0.9997042417526245
ίσαμε 0.9997039437294006
άνθρωπος 0.9997020363807678
τώρα 0.999701976776123
όμως 0.9996985197067261
μικρός 0.9996974468231201
σαν 0.9996969103813171
ανατολή 0.9996965527534485
κυνηγός 0.9996938705444336
μένω 0.9996918439865112
πια 0.9996880292892456
αίμα 0.999687910079956
απάνω 0.9996878504753113
τόπος 0.9996874928474426
μόλις 0.9996874928474426
μέσα 0.99968636035

In [33]:
similar_words_black = model.wv.most_similar('μαύρος', topn=5000)
similar_words_black_filtered = filter_words_by_tfidf(similar_words_black, word_tfidf, tfidf_threshold)
for w in similar_words_black_filtered:
    print(w)

('καρδιά', 0.9985538721084595)
('βγαίνω', 0.9984931945800781)
('κοντά', 0.9984622597694397)
('τέλος', 0.9984619617462158)
('βράδυ', 0.9984510540962219)
('κάποτε', 0.9984503388404846)
('πρωί', 0.9984501600265503)
('μπροστά', 0.9984414577484131)
('μος', 0.9984408020973206)
('ψηλά', 0.9984397888183594)
('μικρός', 0.9984376430511475)
('ακούω', 0.9984349608421326)
('τρέμει', 0.9984230995178223)
('εκεί', 0.9984182715415955)
('κάνω', 0.998416006565094)
('ολοένα', 0.9984111785888672)
('άρτεμος', 0.9984092116355896)
('όλος', 0.9984065890312195)
('όσο', 0.998405933380127)
('μου', 0.9984045624732971)
('μονάχος', 0.9984036087989807)
('δρόμος', 0.9983959197998047)
('παίρνω', 0.9983816146850586)
('ίσαμε', 0.9983795881271362)
('θάλασσα', 0.9983782768249512)
('μεγάλος', 0.9983769655227661)
('τόπος', 0.9983681440353394)
('λος', 0.9983676671981812)
('τότης', 0.9983657598495483)
('έτσι', 0.9983643889427185)
('ουρανός', 0.9983636140823364)
('εκείνος', 0.9983612298965454)
('κάτι', 0.9983600974082947)
('κορ

In [32]:
print(corpus[4])

αηδονοπιτα τoy ιδιoy φραουστ νέος σύνορο λιβάνη νέος έκδοση αναθεωρημένη εκδόσεις πατάκη αποσπασμα βιβλιο ωκεανου εκδόσεις πατάκη νέος έκδοση εκδόσεις πατάκη ψιχος εκεινου καλοκαιριος εκδόσεις πατάκη σκι πεταλουδα εκδόσεις πατάκη αηδονοπιτα εκδόσεις πατάκη ανεμωλιο εκδόσεις πατάκη σκηνος βιο ματιας αλμοσινο εκδόσεις πατάκη λιγες ένας νυχτος εκδόσεις πατάκη ισιδωρος ζουργος αηδονοπιτα μυθιστόρημα θέση υπογραφή δικαιούχου δικαίωμα πνευματικός ιδιοκτησία εφόσον αυτός προβλέπω από σύμβαση παρόν έργο πνευματικός ιδιοκτησία προστατεύω διάταξη ελληνικός μοθεσία όπως έχω τροποποιώ ισχύω σήμερα διεθνής σύμβαση πνευματικός ιδιοκτησία απαγορεύω απόλυτα άνευ γραπτός αδεία εκδότη οποιονδήποτε τρόπος μέσος ηλεκτρονικός μηχανικός άλλος αντιγραφή φωτοανατύπωση γένω αναπαραγωγή εκμίσθωση δανεισμός μετάφραση διασκευή αναμετάδοση κοινός οποιοσδήποτε μορφή γένω εκμετάλλευση συνόλου μέρος έργο eκδόσεις πατάκη σύγχρονη ελληνικός λογοτεχνία πεζογραφία ισίδωρος ζουργός αηδονόπιτα yπεύθυνος έκδοση kώστα γιαννό

In [29]:
for w in all_tokens:
    print(w)

['ηλιο', 'βενεζη']
['ακαδημία', 'αθηνών']
['νούμερο']
['βιβλιο', 'σκλαβια']
['εισαγωγή', 'δημήτρης', 'δασκαλόπουλος']
['τεσσαρακοστος', 'εβδομος', 'εκδοση']
['βιβλιοπωλειον', 'εστια']
['κολλαρο', 'σιος']
['αθηνα']
['νούμερο', 'είμαι', 'ίδιος', 'ταυτότητα', 'συγγραφέα', 'παιδί']
['δεκαοκτώς', 'χρόνος', 'οδηγώ', 'από', 'τούρκους', 'σε ο', 'κάτεργα', 'ανατολή']
['βιβλίο', 'είμαι', 'ένας', 'συγκλονιστικός', 'χρονικός', 'γραμμένος', 'αίμα', 'όπως', 'επισημαίνω']
['βενέζης', 'προσθέτοντα', 'λέω', 'καυτής', 'ύλη', 'σάρκα', 'στάζω']
['αίμα', 'μου', 'πλημμυρίζω', 'σελίδα', 'αρχικός', 'μορφή', 'γράφτηκε']
['ξαναδουλεύτηκε', 'οπότε', 'εκδόθηκε', 'πρώτος', 'φορά', 'επιτυχία']
['σημείωσε', 'είμαι', 'τεράστιος', 'ακόμα', 'έξω', 'από', 'ελληνικός', 'χώρος']
['ηλία', 'βενέζης', 'βιβλίομαρτυρία', 'είμαι', 'γραώνμ', 'πρώτος', 'πρόσωπος']
['πραγματικός', 'όνομα', 'αφηγητήσυγγραφέα', 'γεννήθηκε', 'αβαλίς', 'ήρθε']
['Ελλάδα', 'μικρασιατικός', 'καταστροφή', 'θεωρώ', 'ένας', 'από']
['κυριότερους', 'εκπροσώπο

In [36]:
woman = set(similar_words_woman_filtered) - set(similar_words_man_filtered)
for c in woman:
    print(c)

('ελάχιστος', 0.9988299608230591)
('τραβά', 0.998904824256897)
('σιμώ', 0.9987433552742004)
('μαρτυρία', 0.9943594336509705)
('μιλούσαν', 0.9980311393737793)
('χειρονομία', 0.9729433059692383)
('αλυσίδα', 0.9887266755104065)
('ανθρώπου', 0.9993889927864075)
('τάγμα', 0.998852550983429)
('σκιής', 0.9871140718460083)
('μουσικός', 0.9989537000656128)
('μιαν', 0.9996652007102966)
('κιόλας', 0.9988471269607544)
('απελπισία', 0.9937637448310852)
('κοπελίτσα', 0.9938833117485046)
('νεανικός', 0.9961318373680115)
('πάω', 0.9995177984237671)
('ξύλο', 0.9992819428443909)
('φαμίλια', 0.9967626929283142)
('βρούμε', 0.9960896968841553)
('εκδοσεις', 0.9931181073188782)
('φωνός', 0.9988595843315125)
('αεικίνητος', 0.9986662864685059)
('εξόντωση', 0.9933047294616699)
('γαλήνη', 0.9992061853408813)
('ωραίος', 0.9956719875335693)
('βλέπαμε', 0.997407853603363)
('πάει', 0.9997848868370056)
('ρολογά', 0.9865398406982422)
('ήχος', 0.9996322393417358)
('αριστούργημα', 0.986133337020874)
('έκοψε', 0.99816250

In [39]:
a = set(similar_words_man) - set(similar_words_man_filtered)
for c in a:
    print(c)

('φώναζα', 0.9928625226020813)
('άκουσες', 0.9858298301696777)
('ματόκλαδα', 0.9808874726295471)
('στρέφω', 0.9753026962280273)
('σπάραζε', 0.9930129647254944)
('αφήνεις', 0.9599517583847046)
('στεκόμαστε', 0.9806281328201294)
('ίσκιος', 0.970890462398529)
('θρήνος', 0.9609472751617432)
('πένω', 0.9906597137451172)
('θέλοντα', 0.9910878539085388)
('αποκοιμήθηκαν', 0.9615941047668457)
('πεινούσαν', 0.9730812907218933)
('στείλει', 0.942257821559906)
('γένιο', 0.9906777739524841)
('κοιμήθηκε', 0.9752969741821289)
('κοπαδιού', 0.9113335013389587)
('στρατιωτικός', 0.9739534854888916)
('βλαστήμησε', 0.9854518175125122)
('δροσιά', 0.9668321013450623)
('πιστολιά', 0.9748033881187439)
('κουνά', 0.9235674738883972)
('ξεκολλώ', 0.9665622115135193)
('ερημιάς', 0.9718571305274963)
('παράγκη', 0.9643923044204712)
('παρτίδα', 0.9789111614227295)
('ιερή', 0.9581330418586731)
('ανατολικά', 0.9925541877746582)
('κουνήθηκε', 0.9261179566383362)
('χρήσιμος', 0.9937964081764221)
('αλαλαγμός', 0.93763309717

In [38]:
man = set(similar_words_man_filtered) - set(similar_words_woman_filtered)
for c in man:
    print(c)

('διαφορετικός', 0.9900112152099609)
('γκιαούρ', 0.9947792887687683)
('τού', 0.9760396480560303)
('παίζαν', 0.9961867928504944)
('δείξει', 0.9970225095748901)
('χτυπώντας', 0.9952403903007507)
('αρχαίος', 0.9890667796134949)
('ασπιρίνος', 0.9746025800704956)
('ήρθες', 0.9913895726203918)
('σώπας', 0.9978289604187012)
('βράχος', 0.9990494251251221)
('πνεύμα', 0.9973523020744324)
('πλήθος', 0.9993821382522583)
('μιαν', 0.9995492696762085)
('μακρινός', 0.9993531107902527)
('ποδάρια', 0.9993326663970947)
('σπορ', 0.9973286390304565)
('μοιάζανε', 0.9379456043243408)
('ανατολή', 0.9996965527534485)
('μαφαζάδα', 0.9989628791809082)
('χαλασμός', 0.9879759550094604)
('δάχτυλώ', 0.9540125727653503)
('τύλιξε', 0.9945777654647827)
('απρόοπτος', 0.9926842451095581)
('ολίγος', 0.9715442061424255)
('μυθιστόρημα', 0.88836669921875)
('σημείο', 0.9933940172195435)
('έκλαιγε', 0.9981762170791626)
('καταλαβαίνεις', 0.9899325370788574)
('έμαθε', 0.9988623857498169)
('αργύρη', 0.9992695450782776)
('χάθηκε',